In [1]:
# Импорт всех необходимых модулей для оптимизации
import sys
import os
from pathlib import Path

# Добавляем путь к модулям проекта
project_root = Path.cwd()
src_path = project_root / "src"
sys.path.insert(0, str(src_path))

# Основные модули оптимизации
from optimization import (
    # Основные классы
    OptimizationExecutor,
    OptimizationReporter,
    
    # Хранилище результатов
    InMemoryResultsStore,
    OptimizationResult,
    ResultsStoreProtocol,
    
    # Пространство параметров
    ParameterDefinition,
    ParameterSpace,
    
    # Стратегии поиска
    SearchStrategy,
    GridSearchStrategy,
    RandomSearchStrategy,
)

# Дополнительные импорты для работы с данными и бэктестингом
import pandas as pd
import numpy as np
from typing import Dict, Any, List, Optional, Mapping, Sequence
from dataclasses import dataclass
from datetime import datetime, UTC

# Импорты для работы с сигналами и индикаторами
from signals.base_signal import BaseSignal
from signals.signal_registry import SignalRegistry
from indicators.base_indicator import BaseIndicator
from indicators.indicator_registry import IndicatorRegistry

# Импорты для бэктестинга
from backtest.engine import BacktestEngine
from backtest.metrics import MetricsCalculator
from backtest.trade import Trade
from backtest.commission import CommissionCalculator
from optimization.executor import SignalConfig

print("✅ Все модули оптимизации успешно импортированы!")
print(f"📁 Рабочая директория: {project_root}")
print(f"📦 Доступные стратегии: GridSearchStrategy, RandomSearchStrategy")
print(f"📊 Доступные хранилища: InMemoryResultsStore")
print(f"📈 Доступные репортеры: OptimizationReporter")


✅ Все модули оптимизации успешно импортированы!
📁 Рабочая директория: c:\Users\user\Documents\spreader_pro\code\trend_optimization
📦 Доступные стратегии: GridSearchStrategy, RandomSearchStrategy
📊 Доступные хранилища: InMemoryResultsStore
📈 Доступные репортеры: OptimizationReporter


In [15]:
# Ячейка 1: Импорты и настройка
import sys
sys.path.append('src')
from data import CSVLoader
import pandas as pd
import numpy as np

from lightweight_charts import JupyterChart
# Ячейка 2: Настройка данных
DATA_DIR = r"G:\My Drive\data_fut"
TICKER = "IMOEXF"
loader = CSVLoader(DATA_DIR, use_cache=True)

# Ячейка 3: Загрузка данных
start_date = '2024-01-03'
end_date = '2024-04-03'

timeframe = 10

df = loader.load(TICKER, timeframe=timeframe, start_date=start_date, end_date=end_date)
print(f"Данные: {len(df)} баров, период: {df.index[0]} - {df.index[-1]}")

# Ячейка 4: Ваш анализ (например, Volatility Median)
# Здесь можете использовать функции из VM_base_optimize.py

Данные: 5293 баров, период: 2024-01-03 09:00:00 - 2024-04-02 23:50:00


In [3]:
df.head()

OPEN    HIGH     LOW   CLOSE     VOL
2025-06-16 09:00:00  8591.0  8596.0  8540.0  8549.3  3206.0
2025-06-16 09:05:00  8549.2  8549.9  8509.0  8509.6  6828.0
2025-06-16 09:10:00  8510.0  8510.0  8500.0  8508.0  5228.0
2025-06-16 09:15:00  8508.0  8517.0  8496.0  8508.9  4216.0
2025-06-16 09:20:00  8502.2  8518.5  8494.8  8500.0  3346.0

In [4]:
display(df['CLOSE'].agg(
    min_price='min',
    max_price='max',
    avg_price='mean',
    median_price='median',
    std_price='std',
    var_price='var',
    n='count'
))


min_price         8177.500000
max_price         9905.600000
avg_price         8645.722483
median_price      8536.800000
std_price          407.466059
var_price       166028.589622
n                12325.000000
Name: CLOSE, dtype: float64

In [5]:
# Простая функция вместо класса SignalFactory
def create_signal_config(parameters):
    """Разделяем параметры по назначению"""
    params = parameters or {}
    signal_name = params.get('signal', 'SlopeSignal')
    signal_instance = SignalRegistry.get(signal_name)
    default_signal_params = {
        'DeviationSignal': {'offset': 12},
        'SlopeSignal': {'threshold': 0.0001},
    }
    signal_params = default_signal_params.get(signal_name, {}).copy()
    for key in ('offset', 'threshold'):
        value = params.get(key)
        if value is not None:
            signal_params[key] = value
    return SignalConfig(
        signal=signal_instance,
        signal_params=signal_params,
        indicator_params={
            'KATR': params.get('katr'),
            'PerATR': params.get('peratr'),
            'SMA': params.get('sma'),
            'MinRA': params.get('minra'),
            'FlATR': params.get('flatr'),
            'FlHL': params.get('flhl')
        },
        backtest_params={
            # entry_price_type/n_contracts можно переопределить здесь при необходимости
            # 'entry_price_type': 'close',
            # 'n_contracts': 1,
        }
    )


# Простая функция вместо класса IndicatorBuilder
def build_indicator(df, params, *, verbose=False):
    """Создаем индикатор VolatilityMedian с фильтрацией параметров"""
    vm_ind = IndicatorRegistry.get('VolatilityMedian')

    param_mapping = {
        'katr': 'KATR',
        'peratr': 'PerATR',
        'sma': 'SMA',
        'minra': 'MinRA',
        'flatr': 'FlATR',
        'flhl': 'FlHL',
    }

    indicator_params = {}
    for param_key, param_value in (params or {}).items():
        normalized_key = str(param_key).lower()
        mapped_key = param_mapping.get(normalized_key)
        if mapped_key and param_value is not None:
            indicator_params[mapped_key] = param_value

    if verbose:
        print(f'Параметры для индикатора: {indicator_params}')

    return vm_ind.calculate(df, **indicator_params)


In [6]:
# Простой способ - создание из ваших данных
your_params = {
    "KATR": [3, 4, 5, 6, 7, 8, 9, 10, 11],
    "PerATR": [5, 10, 40, 80], 
    "SMA": [1, 2, 3, 5, 9, 15],
    "MinRA": [0],
    "FlATR": [0],
    "FlHL": [0],
    "SlopeSignal": [0.0001],
}

# Преобразование в ParameterSpace
definitions = []
for name, values in your_params.items():
    definitions.append(ParameterDefinition(
        name=name.lower(),  # приводим к нижнему регистру
        values=values
    ))

parameter_space = ParameterSpace.from_definitions(definitions)

In [7]:
# Создаем оптимизатор
executor = OptimizationExecutor(
    backtest_engine=BacktestEngine(),
    parameter_space=parameter_space,
    strategy=GridSearchStrategy(parameter_space),
    signal_factory=create_signal_config,  # ← Простая функция!
    results_store=InMemoryResultsStore(),
    indicator_builder=build_indicator,    # ← Простая функция!
    # ↓↓↓ новые настройки производительности/стабильности ↓↓↓
    checkpoint_interval=1000,              # было 1 → станет реже и быстрее
    per_candidate_timeout=None,           # убрать пер-кандидатные пулы
    default_max_workers=1,                # дефолт: одиночный режим
    checkpoint_enabled=False,               # оставить включённым (но с редким интервалом)
    persist_results=False             # только память (без файловых операций)
    
)

print("✅ Оптимизатор создан!")

✅ Оптимизатор создан!


#### модуль для построения графика 📈

In [8]:
# result_indices = [88]
# verbose = True

from itertools import cycle

_BOKEH_OUTPUT_NOTEBOOK_LOADED = globals().get('_BOKEH_OUTPUT_NOTEBOOK_LOADED', False)

def _ensure_bokeh_inline():
    """Загружает BokehJS inline, чтобы графики отображались без доступа к CDN."""
    global _BOKEH_OUTPUT_NOTEBOOK_LOADED
    if not _BOKEH_OUTPUT_NOTEBOOK_LOADED:
        from bokeh.io import output_notebook
        from bokeh.resources import INLINE
        output_notebook(resources=INLINE, verbose=False, hide_banner=True)
        _BOKEH_OUTPUT_NOTEBOOK_LOADED = True

def _collect_indicator_params(parameters):
    """Преобразует параметры результата в формат индикатора VolatilityMedian."""
    mapping = {
        'katr': 'KATR',
        'peratr': 'PerATR',
        'sma': 'SMA',
        'minra': 'MinRA',
        'flatr': 'FlATR',
        'flhl': 'FlHL',
    }
    extracted = {}
    for raw_key, value in (parameters or {}).items():
        key = mapping.get(str(raw_key).lower())
        if key and value is not None:
            extracted[key] = value
    return extracted

def _ensure_series(signals, index):
    """Возвращает Series с сигналами, выровненными по индексу цен."""
    import pandas as pd
    if hasattr(signals, 'index'):
        series = signals.reindex(index)
        return series.ffill().fillna(0)
    return pd.Series(signals, index=index).fillna(0)

def _run_backtest_for_result(result_index, *, verbose=True):
    """Пересчитывает бэктест для выбранного результата и возвращает данные."""
    if not 0 <= result_index < len(results):
        if verbose:
            print(f"Ошибка: индекс {result_index} вне диапазона доступных результатов (0..{len(results) - 1})")
        return None

    target_result = results[result_index]
    signal_config = create_signal_config(target_result.parameters)

    indicator_series = getattr(signal_config, 'indicator', None)
    if indicator_series is None:
        indicator_series = build_indicator(df, target_result.parameters, verbose=verbose)
    if indicator_series is not None and hasattr(indicator_series, 'reindex'):
        indicator_series = indicator_series.reindex(df.index).ffill()

    raw_signals = signal_config.signal.generate(df, indicator_series, **signal_config.signal_params)
    signals = _ensure_series(raw_signals, df.index)

    backtest_engine = BacktestEngine()
    backtest_params = dict(getattr(signal_config, 'backtest_params', {}))
    backtest_result = backtest_engine.run(df, signals, **backtest_params)

    return {
        'result_index': result_index,
        'target_result': target_result,
        'indicator_params': _collect_indicator_params(target_result.parameters),
        'signals': signals,
        'backtest_result': backtest_result,
        'equity': backtest_result.get('equity'),
    }

def build_equity_for_result(result_index, *, verbose=True):
    """Строит эквити для отдельного результата и выводит ключевые метрики."""
    run_data = _run_backtest_for_result(result_index, verbose=verbose)
    if not run_data:
        return None

    target_result = run_data['target_result']
    backtest_result = run_data['backtest_result']
    equity = run_data['equity']

    print(f"Строим эквити для результата #{result_index}")
    print(
        "Метрики из оптимизации: Total Return={:.4f}, Max DD={:.4f}".format(
            target_result.metrics.get('total_return', 0),
            target_result.metrics.get('max_drawdown', 0),
        )
    )

    if equity is not None:
        print(f"Эквити построена: {len(equity)} точек")
        print(
            "Повторный бэктест: Total Return={:.4f}, Max DD={:.4f}".format(
                backtest_result.get('total_return', 0),
                backtest_result.get('max_drawdown', 0),
            )
        )
        return equity

    print('Ошибка: не удалось получить эквити из результата бэктеста')
    return None

def plot_equities_for_results(result_indices, *, verbose=True):
    """Строит один график с эквити и таблицу метрик для выбранных индексов."""
    if not result_indices:
        print('Список индексов пуст. Укажите хотя бы один индекс результата.')
        return None

    prepared_runs = []
    for idx in result_indices:
        run_data = _run_backtest_for_result(idx, verbose=verbose)
        if run_data and run_data.get('equity') is not None:
            prepared_runs.append(run_data)

    if not prepared_runs:
        print('Не удалось построить эквити ни для одного из выбранных индексов.')
        return None

    _ensure_bokeh_inline()

    from bokeh.layouts import column
    from bokeh.models import ColumnDataSource, DataTable, NumberFormatter, TableColumn, HoverTool
    from bokeh.palettes import Category10, Category20, Turbo256
    from bokeh.plotting import figure
    from bokeh.io import show

    n = len(prepared_runs)
    if n <= 10:
        palette = list(Category10[10][:n])
    elif n <= 20:
        palette = list(Category20[20][:n])
    else:
        step = max(len(Turbo256) // n, 1)
        palette = [Turbo256[(i * step) % len(Turbo256)] for i in range(n)]
    color_cycle = cycle(palette)

    p = figure(
        title=f"Equity Curve (индексы: {result_indices})",
        x_axis_type='datetime',
        width=900,
        height=420,
        tools='pan,wheel_zoom,box_zoom,reset,save'
    )
    p.add_tools(HoverTool(tooltips=[('Время', '@x{%F %T}'), ('Эквити', '@y{0.00}')], formatters={'@x': 'datetime'}))

    table_rows = {
        'result_index': [],
        'indicator': [],
        'total_return': [],
        'max_drawdown': [],
        'n_trades': [],
        'wave_ratio': [],
    }

    for run_data, color in zip(prepared_runs, color_cycle):
        equity = run_data['equity']
        metrics = run_data['backtest_result']
        label = f"Equity #{run_data['result_index']}"
        p.line(equity.index, equity.values, line_width=2, color=color, legend_label=label)

        table_rows['result_index'].append(run_data['result_index'])
        indicator_description = ', '.join(f"{k}={v}" for k, v in run_data['indicator_params'].items()) or '—'
        table_rows['indicator'].append(indicator_description)
        table_rows['total_return'].append(metrics.get('total_return', float('nan')))
        table_rows['max_drawdown'].append(metrics.get('max_drawdown', float('nan')))
        table_rows['n_trades'].append(metrics.get('n_trades', float('nan')))
        wave_ratio = metrics.get('mean_wave_mfe_ratio')
        if wave_ratio is None:
            wave_ratio = metrics.get('wave_ratio')
        table_rows['wave_ratio'].append(wave_ratio if wave_ratio is not None else float('nan'))

    p.legend.location = 'top_left'
    p.legend.click_policy = 'hide'
    p.grid.grid_line_alpha = 0.25
    p.xaxis.axis_label = 'Время'
    p.yaxis.axis_label = 'Эквити'

    source = ColumnDataSource(table_rows)
    columns = [
        TableColumn(field='result_index', title='Индекс результата'),
        TableColumn(field='indicator', title='Параметры индикатора'),
        TableColumn(field='total_return', title='Total Return', formatter=NumberFormatter(format='0.0000')),
        TableColumn(field='max_drawdown', title='Max DD', formatter=NumberFormatter(format='0.0000')),
        TableColumn(field='n_trades', title='N trades', formatter=NumberFormatter(format='0')),
        TableColumn(field='wave_ratio', title='Wave ratio', formatter=NumberFormatter(format='0.0000')),
    ]

    data_table = DataTable(
        source=source,
        columns=columns,
        width=900,
        height=220,
        index_position=None,
        autosize_mode='fit_columns'
    )

    show(column(p, data_table))

    print(f"Эквити построены для индексов: {[run['result_index'] for run in prepared_runs]}")
    return prepared_runs


# runs_summary = plot_equities_for_results(result_indices, verbose=verbose)


#### модуль расчета времени оптимизации

In [9]:
import time
# === ЗАПУСКАЕМ ОПТИМИЗАЦИЮ ===
print("🚀 Начинаем оптимизацию...")
start_time = time.time()

run_dir = executor.run(df)  # фиксируем одиночный воркер

end_time = time.time()
actual_time = end_time - start_time

# === РЕЗУЛЬТАТЫ ===
results = list(executor.results_store)
print(f"✅ Завершено! Получено {len(results)} результатов")
print(f"⏱️ Фактическое время: {actual_time:.1f} сек ({actual_time/60:.1f} мин)")
print(f"📊 Скорость: {len(results)/actual_time:.1f} комбинаций/сек")
best_result = max(results, key=lambda r: r.metrics.get('total_return', 0))
print(f"🏆 Лучший результат: {best_result.parameters}")
print(f"📊 Метрики: {best_result.metrics}")
print(f"📁 Директория запуска: {run_dir}")

🚀 Начинаем оптимизацию...
✅ Завершено! Получено 216 результатов
⏱️ Фактическое время: 76.6 сек (1.3 мин)
📊 Скорость: 2.8 комбинаций/сек
🏆 Лучший результат: {'katr': 6, 'peratr': 5, 'sma': 15, 'minra': 0, 'flatr': 0, 'flhl': 0, 'slopesignal': 0.0001}
📊 Метрики: {'total_return': 0.011161749339999805, 'max_drawdown': 0.0028214339399049715, 'recovery_factor': 3.9560555298259943, 'sharpe': 0.25123921765528373, 'sortino': 0.3217593569523921, 'area_ab': 0.0030220592628181805, 'n_flips': 27, 'n_trades': 28, 'win_rate': 0.5714285714285714, 'profit_factor': 2.7000618571695774, 'waves_count': 27, 'mean_wave_mfe': 126.08888888888895, 'mean_wave_mfe_ratio': 2.6937915491991493}
📁 Директория запуска: output\optimization\20251113_160651


In [16]:
# === ТАБЛИЦА РЕЗУЛЬТАТОВ ТЕСТИРОВАНИЯ ===
import pandas as pd

# Создаем DataFrame с результатами
results_data = []
for i, result in enumerate(results):
    row = {
        'Индекс': i,
        'KATR': result.parameters.get('katr'),
        'PerATR': result.parameters.get('peratr'), 
        'SMA': result.parameters.get('sma'),
        #'offset': result.parameters.get('offset'),
        'threshold': result.parameters.get('threshold'),
        'Total Return': result.metrics.get('total_return', 0),
        'Max Drawdown': result.metrics.get('max_drawdown', 0),
        'Recovery Factor': result.metrics.get('recovery_factor', 0),
        'Sharpe': result.metrics.get('sharpe', 0),
        'Sortino': result.metrics.get('sortino', 0),
        'Win Rate': result.metrics.get('win_rate', 0),
        'Profit Factor': result.metrics.get('profit_factor', 0),
        'AreaAB': result.metrics.get('area_ab', 0),
        'N Trades': result.metrics.get('n_trades', 0),
        'Wave_ratio': result.metrics.get('mean_wave_mfe_ratio', 0)
    }
    results_data.append(row)

# Создаем DataFrame и сортируем по Total Return
results_df = pd.DataFrame(results_data)
results_df = results_df.sort_values('Total Return', ascending=False).reset_index(drop=True)

print("📊 ТАБЛИЦА РЕЗУЛЬТАТОВ ОПТИМИЗАЦИИ")
print("=" * 80)
print(f"Всего результатов: {len(results_df)}")
print(f"Лучший результат (индекс {results_df.index[0]}):")
print(f"  Total Return: {results_df.iloc[0]['Total Return']:.4f}")
print(f"  Max Drawdown: {results_df.iloc[0]['Max Drawdown']:.4f}")
print(f"  Sharpe: {results_df.iloc[0]['Sharpe']:.4f}")
print("=" * 80)

# Отображаем топ-10 результатов
print("\n🏆 ТОП-10 РЕЗУЛЬТАТОВ:")
display(results_df.head(50).round(4))


📊 ТАБЛИЦА РЕЗУЛЬТАТОВ ОПТИМИЗАЦИИ
Всего результатов: 216
Лучший результат (индекс 0):
  Total Return: 0.0112
  Max Drawdown: 0.0028
  Sharpe: 0.2512

🏆 ТОП-10 РЕЗУЛЬТАТОВ:


Индекс  KATR  PerATR  SMA threshold  Total Return  Max Drawdown  \
0       77     6       5   15      None        0.0112        0.0028   
1      146     9       5    3      None        0.0109        0.0035   
2      145     9       5    2      None        0.0107        0.0034   
3      144     9       5    1      None        0.0107        0.0036   
4      169    10       5    2      None        0.0106        0.0041   
5       14     3      40    3      None        0.0104        0.0051   
6      168    10       5    1      None        0.0103        0.0043   
7      142     8      80    9      None        0.0095        0.0048   
8      171    10       5    5      None        0.0094        0.0055   
9      149     9       5   15      None        0.0093        0.0053   
10     101     7       5   15      None        0.0093        0.0048   
11      18     3      80    1      None        0.0093        0.0031   
12     170    10       5    3      None        0.0089        0.0054   
13     150     9      10    1      None        0.0089        0.0056   
14      10     3      10    9      None        0.0088        0.0046   
15     147     9       5    5      None        0.0086        0.0058   
16     195    11       5    5      None        0.0081        0.0066   
17     151     9      10    2      None        0.0080        0.0058   
18     125     8       5   15      None        0.0079        0.0057   
19     135     8      40    5      None        0.0079        0.0037   
20     124     8       5    9      None        0.0079        0.0052   
21     143     8      80   15      None        0.0077        0.0056   
22     152     9      10    3      None        0.0077        0.0058   
23     153     9      10    5      None        0.0076        0.0054   
24     197    11       5   15      None        0.0076        0.0037   
25      19     3      80    2      None        0.0075        0.0044   
26      21     3      80    5      None        0.0075        0.0055   
27     103     7      10    2      None        0.0074        0.0039   
28     162     9      80    1      None        0.0073        0.0058   
29      30     4      10    1      None        0.0073        0.0046   
30     192    11       5    1      None        0.0073        0.0065   
31     132     8      40    1      None        0.0072        0.0044   
32     130     8      10    9      None        0.0072        0.0069   
33     110     7      40    3      None        0.0072        0.0035   
34      20     3      80    3      None        0.0072        0.0054   
35     136     8      40    9      None        0.0072        0.0038   
36      15     3      40    5      None        0.0072        0.0048   
37     163     9      80    2      None        0.0071        0.0060   
38     193    11       5    2      None        0.0071        0.0066   
39     181    10      40    2      None        0.0071        0.0052   
40     196    11       5    9      None        0.0071        0.0052   
41     194    11       5    3      None        0.0071        0.0066   
42     178    10      10    9      None        0.0071        0.0044   
43     166     9      80    9      None        0.0071        0.0055   
44     133     8      40    2      None        0.0070        0.0046   
45     172    10       5    9      None        0.0070        0.0060   
46       3     3       5    5      None        0.0070        0.0067   
47     180    10      40    1      None        0.0070        0.0054   
48     164     9      80    3      None        0.0069        0.0061   
49     109     7      40    2      None        0.0068        0.0035   

    Recovery Factor  Sharpe  Sortino  Win Rate  Profit Factor  AreaAB  \
0            3.9561  0.2512   0.3218    0.5714         2.7001  0.0030   
1            3.1567  0.2455   0.3218    0.4667         2.6858  0.0024   
2            3.1388  0.2408   0.3142    0.4688         2.4622  0.0024   
3            2.9414  0.2402   0.3145    0.4412         2.4472  0.0024   
4            2.60

In [ ]:
results_df.to_csv('optimization_results2024.csv', index=False)

In [11]:
factor = 'KATR'
# First group by KATR and get top 4 from each group
top_by_katr = results_df.groupby(factor, as_index=False).apply(
    lambda x: x.nlargest(1, 'Total Return')
).reset_index(drop=True)

# Calculate average return for each KATR group
avg_returns = top_by_katr.groupby(factor)['Total Return'].mean().reset_index()
avg_returns.columns = [factor, 'Average_return_group']

# Merge the average returns back to the main dataframe
top_by_katr = top_by_katr.merge(avg_returns, on=factor, how='left')

# Sort by Average_return_group (descending) and then by Total Return (descending)
top_by_katr = top_by_katr.sort_values(['Average_return_group', 'Total Return'], 
                                     ascending=[False, False])

display(top_by_katr)

C:\Users\user\AppData\Local\Temp\ipykernel_21872\2887335241.py:3: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  top_by_katr = results_df.groupby(factor, as_index=False).apply(


Индекс  KATR  PerATR  SMA threshold  Total Return  Max Drawdown  \
3      77     6       5   15      None      0.011162      0.002821   
6     146     9       5    3      None      0.010909      0.003456   
7     169    10       5    2      None      0.010613      0.004078   
0      14     3      40    3      None      0.010403      0.005083   
5     142     8      80    9      None      0.009512      0.004756   
4     101     7       5   15      None      0.009278      0.004791   
8     195    11       5    5      None      0.008109      0.006581   
1      30     4      10    1      None      0.007303      0.004595   
2      50     5       5    3      None      0.005302      0.005443   

   Recovery Factor    Sharpe   Sortino  Win Rate  Profit Factor    AreaAB  \
3         3.956056  0.251239  0.321759  0.571429       2.700062  0.003022   
6         3.156723  0.245531  0.321824  0.466667       2.685785  0.002367   
7         2.602701  0.238798  0.312126  0.464286       2.673783  0.002698   
0         2.046724  0.233349  0.305218  0.423913       1.610790  0.002579   
5         1.999776  0.214098  0.282312  0.625000       2.790506  0.004141   
4         1.936609  0.208865  0.275101  0.464286       2.172862  0.003130   
8         1.232248  0.182785  0.244117  0.384615       2.027837  0.002628   
1         1.589395  0.164151  0.213467  0.397260       1.521822  0.002928   
2         0.974143  0.119538  0.156055  0.387097       1.366842  0.002144   

   N Trades  Wave_ratio  Average_return_group  
3        28    2.693792              0.011162  
6        30    2.995991              0.010909  
7        28    2.510693              0.010613  
0        92    7.285352              0.010403  
5        16    7.562178              0.009512  
4        28    4.291075              0.009278  
8        26    2.374669              0.008109  
1        73    2.567358              0.007303  
2        62    3.434203              0.005302

In [ ]:
mask = (
    (results_df['KATR'] == 4) &
    (results_df['PerATR'] == 30) &
    (results_df['SMA'] == 2)
)
row = results_df.loc[mask]
row

In [24]:
eq = list(top_by_katr['Индекс'])
eq10 = list(results_df.head(10)['Индекс'])
eq

[10, 36, 169, 103, 147, 197, 77, 136, 60]

In [27]:
selected = eq
plot_equity_curves(selected, title="Top-3 strategies", verbose=False)

Начальная эквити  Конечная эквити  Доходность %  Макс. просадка %
Индекс                                                                   
10              100000.0        102600.54          2.60              0.59
36              100000.0        102202.94          2.20              1.28
169             100000.0        101837.63          1.84              1.28
103             100000.0        101766.28          1.77              0.79
147             100000.0        101764.04          1.76              1.00
197             100000.0        101621.32          1.62              1.07
77              100000.0        101472.07          1.47              1.45
136             100000.0        101459.78          1.46              0.96
60              100000.0        101131.89          1.13              0.97

Начальная эквити  Конечная эквити  Доходность %  Макс. просадка %
Индекс                                                                   
10              100000.0    102600.544659      2.600545          0.588567
36              100000.0    102202.940488      2.202940          1.280141
169             100000.0    101837.634070      1.837634          1.277987
103             100000.0    101766.278024      1.766278          0.793911
147             100000.0    101764.044901      1.764045          0.998507
197             100000.0    101621.321555      1.621322          1.074401
77              100000.0    101472.067801      1.472068          1.447267
136             100000.0    101459.784862      1.459785          0.962516
60              100000.0    101131.891870      1.131892          0.968415

In [26]:
result_index = 88
# === ПЕРЕЗАГРУЗКА ФУНКЦИЙ (ВАЖНО!) ===
# build_indicator и create_signal_config определены выше; повторный запуск ячейки гарантирует их наличие в сессии.
print("⚙️ Функции create_signal_config и build_indicator загружены из ранних ячеек.")
def _ensure_series(signals, index):
    """Приводим сигналы к Series с корректным индексом"""
    if hasattr(signals, "index"):
        return signals
    import pandas as pd
    return pd.Series(signals, index=index)


# === ПОСТРОЕНИЕ ЭКВИТИ ПО ИНДЕКСУ РЕЗУЛЬТАТА ===
def build_equity_for_result(result_index, *, verbose=True):
    """Строит эквити для результата по индексу"""
    if not 0 <= result_index < len(results):
        if verbose:
            print(f"❌ Ошибка: Индекс {result_index} выходит за пределы доступных результатов (0..{len(results) - 1})")
        return None

    # Получаем результат по индексу
    target_result = results[result_index]
    if verbose:
        print(f"📊 Строим эквити для результата #{result_index}")
        print(
            "Метрики: Total Return={:.4f}, Max DD={:.4f}".format(
                target_result.metrics.get('total_return', 0),
                target_result.metrics.get('max_drawdown', 0)
            )
        )

    # Создаем конфигурацию сигнала для этого результата
    signal_config = create_signal_config(target_result.parameters)

    # Строим индикатор
    indicator_data = build_indicator(df, target_result.parameters, verbose=verbose)
    indicator_series = getattr(signal_config, 'indicator', None) or indicator_data
    if indicator_series is not None and hasattr(indicator_series, "reindex"):
        indicator_series = indicator_series.reindex(df.index).ffill()

    # Генерируем сигналы на основе конфигурации
    raw_signals = signal_config.signal.generate(df, indicator_series, **signal_config.signal_params)
    signals = _ensure_series(raw_signals, df.index)

    # Создаем бэктест движок и применяем параметры из конфигурации
    backtest_engine = BacktestEngine()
    backtest_params = dict(getattr(signal_config, 'backtest_params', {}))
    backtest_result = backtest_engine.run(df, signals, **backtest_params)

    # Извлекаем эквити
    equity = backtest_result.get('equity')
    if equity is not None:
        if verbose:
            print(f"✅ Эквити построена: {len(equity)} точек")
            print(
                "Повторный бэктест: Total Return={:.4f}, Max DD={:.4f}".format(
                    backtest_result.get('total_return', 0),
                    backtest_result.get('max_drawdown', 0)
                )
            )
        return equity

    if verbose:
        print("❌ Ошибка: Не удалось получить эквити из результата бэктеста")
    return None


def plot_equity_curves(strategy_indices, *, title=None, palette=None, width=900, height=420, verbose=False):
    """Отображает эквити для списка индексов стратегий на одном графике."""
    import numpy as np
    import pandas as pd
    from bokeh.plotting import figure, show, output_notebook
    from bokeh.models import HoverTool, ColumnDataSource
    from bokeh.palettes import Category10, Turbo256
    from IPython.display import display

    if isinstance(strategy_indices, pd.Series):
        indices = strategy_indices.tolist()
    elif hasattr(strategy_indices, 'tolist') and not isinstance(strategy_indices, (list, tuple)):
        try:
            indices = list(strategy_indices)
        except TypeError:
            indices = [strategy_indices]
    elif isinstance(strategy_indices, (list, tuple, set)):
        indices = list(strategy_indices)
    else:
        indices = [strategy_indices]

    unique_indices = []
    for raw_idx in indices:
        try:
            idx = int(raw_idx)
        except (TypeError, ValueError):
            if verbose:
                print(f"⚠️ Пропускаем некорректный индекс: {raw_idx!r}")
            continue
        if idx not in unique_indices:
            unique_indices.append(idx)

    if not unique_indices:
        if verbose:
            print("⚠️ Нет допустимых индексов стратегий для отображения.")
        return None

    curves = []
    stats_rows = []
    for idx in unique_indices:
        equity_series = build_equity_for_result(idx, verbose=verbose)
        if equity_series is None or (hasattr(equity_series, 'empty') and equity_series.empty):
            if verbose:
                print(f"⚠️ Эквити для стратегии #{idx} не построена.")
            continue
        series = equity_series.sort_index()
        curves.append((idx, series))

        start_value = float(series.iloc[0])
        end_value = float(series.iloc[-1])
        cumulative_max = series.cummax()
        drawdown = ((cumulative_max - series) / cumulative_max).replace([np.inf, -np.inf], 0.0).fillna(0.0)
        max_drawdown = float(drawdown.max() * 100)

        stats_rows.append({
            'Индекс': idx,
            'Начальная эквити': start_value,
            'Конечная эквити': end_value,
            'Доходность %': (end_value / start_value - 1) * 100 if start_value else np.nan,
            'Макс. просадка %': max_drawdown,
        })

    if not curves:
        if verbose:
            print("⚠️ Не удалось построить эквити ни для одной стратегии.")
        return None

    def _resolve_palette(n, custom_palette):
        if custom_palette:
            palette_list = list(custom_palette)
            if len(palette_list) < n:
                repeats = (n + len(palette_list) - 1) // len(palette_list)
                palette_list = (palette_list * repeats)[:n]
            return palette_list
        if n <= 10:
            return Category10[10][:n]
        step = max(len(Turbo256) // n, 1)
        return [Turbo256[i * step] for i in range(n)]

    colors = _resolve_palette(len(curves), palette)

    output_notebook(hide_banner=True)

    plot_title = title or "Эквити выбранных стратегий"
    p = figure(
        title=plot_title,
        x_axis_type='datetime',
        width=width,
        height=height,
        tools='pan,wheel_zoom,box_zoom,reset,save'
    )

    hover = HoverTool(
        tooltips=[
            ("Стратегия", "@strategy"),
            ("Время", "@x{%F %T}"),
            ("Эквити", "@y{0.00}")
        ],
        formatters={"@x": "datetime"},
        mode="vline"
    )
    p.add_tools(hover)

    for color, (idx, series) in zip(colors, curves):
        source = ColumnDataSource({
            'x': series.index,
            'y': series.values,
            'strategy': [f'#{idx}'] * len(series),
        })
        p.line('x', 'y', source=source, line_width=2, line_color=color, legend_label=f'#{idx}')

    p.legend.location = 'top_left'
    p.legend.click_policy = 'hide'
    p.grid.grid_line_alpha = 0.25
    p.xaxis.axis_label = 'Время'
    p.yaxis.axis_label = 'Эквити'

    show(p)

    if stats_rows:
        stats_df = pd.DataFrame(stats_rows).set_index('Индекс')
        display(stats_df.round(2))
        return stats_df

    return p


# === ИНТЕРАКТИВНОЕ ПОСТРОЕНИЕ ЭКВИТИ ===
# Введите индекс результата для построения эквити (0-83)
# result_index = 54  # ← ИЗМЕНИТЕ ЭТО ЗНАЧЕНИЕ НА НУЖНЫЙ ИНДЕКС
verbose = True

equity = build_equity_for_result(result_index, verbose=verbose)

if equity is not None:
    print(f"📈 Эквити готова для отображения: {len(equity)} точек")
    print(f"Начальное значение: {equity.iloc[0]:.2f}")
    print(f"Конечное значение: {equity.iloc[-1]:.2f}")
    print(f"Максимум: {equity.max():.2f}")
    print(f"Минимум: {equity.min():.2f}")
else:
    print("❌ Не удалось построить эквити")

# Пример: plot_equity_curves(results_df.head(3)['Индекс'])


⚙️ Функции create_signal_config и build_indicator загружены из ранних ячеек.
📊 Строим эквити для результата #88
Метрики: Total Return=-0.0124, Max DD=0.0231
Параметры для индикатора: {'KATR': 6, 'PerATR': 40, 'SMA': 9, 'MinRA': 0, 'FlATR': 0, 'FlHL': 0}
✅ Эквити построена: 29675 точек
Повторный бэктест: Total Return=-0.0124, Max DD=0.0231
📈 Эквити готова для отображения: 29675 точек
Начальное значение: 100000.00
Конечное значение: 98764.54
Максимум: 100060.79
Минимум: 97749.53


In [ ]:
# === ОТОБРАЖЕНИЕ ЭКВИТИ С BOKEH ===
if equity is not None:
    from bokeh.plotting import figure, show, output_notebook
    from bokeh.models import HoverTool
    
    output_notebook()
    
    # Создаем график
    p = figure(
        title=f'Equity Curve (Результат #{result_index})', 
        x_axis_type='datetime', 
        width=900, 
        height=420, 
        tools='pan,wheel_zoom,box_zoom,reset,save'
    )
    
    # Добавляем линию эквити
    p.line(equity.index, equity.values, line_width=2, color='#2962FF', legend_label='Equity')
    
    # Настраиваем hover
    p.add_tools(HoverTool(
        tooltips=[
            ('Время', '@x{%F %T}'), 
            ('Эквити', '@y{0.00}')
        ], 
        formatters={'@x': 'datetime'}
    ))
    
    # Настройки графика
    p.legend.location = 'top_left'
    p.grid.grid_line_alpha = 0.25
    p.xaxis.axis_label = 'Время'
    p.yaxis.axis_label = 'Эквити'
    
    # Показываем график
    show(p)
    
    # Дополнительная статистика
    print(f"\n📊 СТАТИСТИКА ЭКВИТИ:")
    print(f"  Начальная эквити: {equity.iloc[0]:.2f}")
    print(f"  Конечная эквити: {equity.iloc[-1]:.2f}")
    print(f"  Общая доходность: {(equity.iloc[-1] / equity.iloc[0] - 1) * 100:.2f}%")
    print(f"  Максимальная эквити: {equity.max():.2f}")
    print(f"  Минимальная эквити: {equity.min():.2f}")
    print(f"  Максимальная просадка: {((equity.cummax() - equity) / equity.cummax()).max() * 100:.2f}%")
else:
    print("❌ Эквити не построена. Сначала выполните предыдущую ячейку.")
